In [ ]:
from pathlib import Path
import os
import time
import re
import subprocess
import threading
import sys

install_path=f"{os.environ['HOME']}/sdwebui" # 安装目录
output_path=f"{os.environ['HOME']}/sdwebui/Output" # 输出目录 如果使用google云盘 会在google云盘增加sdwebui/Output
input_path = '/kaggle/input' # 输入目录

venvPath = '/kaggle/input/sd-webui-venv/venv.tar.bak' # 安装好的python环境 sd-webui-venv是一个公开是数据集 可以搜索添加

# 用于使用kaggle api的token文件 参考 https://www.kaggle.com/docs/api
# 此文件用于自动上传koishi的相关配置 也可以用于保存重要的输出文件
kaggleApiTokenFile = '/kaggle/input/configs/kaggle.json'

google_drive = '' 
# 连接谷歌云
try:
    if useGooglrDrive:
        from google.colab import drive
        drive.mount(f'~/google_drive')
        #@title ### 连接到谷歌云并链接文件
        !mkdir -p ~/drive
        !ln -s -rf ~/drive/MyDrive ~/drive
        google_drive = f"{os.environ['HOME']}/drive"
        output_path = f'{google_drive}/sdwebui/Output'
        input_path = f'{google_drive}/sdwebui/Input'
        !mkdir -p {input_path}
except:
    useGooglrDrive = False

!mkdir -p {install_path}
!mkdir -p {output_path}

os.environ['install_path'] = install_path
os.environ['output_path'] = output_path
os.environ['google_drive'] = google_drive

# 不常用配置项
---

In [ ]:
ngrokTokenFile = os.path.join(input_path,'configs/ngrok_token.txt') # 非必填 存放ngrokToken的文件的路径
frpcConfigFile = os.path.join(input_path,'configs/frpc_koishi.ini')  # 非必填 frp 配置文件
# ss证书目录 下载nginx的版本，把pem格式改成crt格式
frpcSSLFFlies =[os.path.join(input_path,'configs/koishi_ssl')]
# frpc 文件目录 如果目录不存在，会自动下载，也可以在数据集搜索 viyiviyi/utils 添加
frpcExePath = os.path.join(input_path,'utils-tools/frpc')

In [ ]:
# 模型目录 文件名称:链接的方式指定文件名
modelDirs = []+[item.strip() for item in 模型列表.split('\n') if item.strip() ]
# vae列表
modelVaeDirs = []+[item.strip() for item in VAE列表.split('\n') if item.strip()]
# 此配置内的目录下所有文件将加载到hypernetworks文件夹
hypernetworksModelDirs = []+[item.strip() for item in hypernetworks列表.split('\n') if item.strip()] 
# 此配置内的目录下所有文件将加载到embeddings文件夹
embeddingsModelDirs = [] +[item.strip() for item in embeddings列表.split('\n') if item.strip()]
# 此配置内的目录下所有文件将加载到Lora文件夹
loraModelDirs = []+[item.strip() for item in Lora列表.split('\n') if item.strip()] 

lyCORISModelDirs = []+[item.strip() for item in LyCORIS列表.split('\n') if item.strip()] 
# controlNet插件模型列表
controlNetModels=[] +[item.strip() for item in controlNet模型列表.split('\n') if item.strip()]
# 插件列表
extensions=[]+[item.strip() for item in 插件列表.split('\n') if item.strip()]
# 配置文件链接
linkHypernetworksDir=False # 链接 hypernetworks 目录到输出目录
linkEmbeddingsDir=False # 链接 embeddings 目录到输出目录
linkTextual_inversionDir=False # 链接 textual_inversion 目录到输出目录 如果需要保存训练过程的产出文件时建议开启

# 其他需要加载的启动参数 写到【参数列表】这个配置去
otherArgs = ' '.join([item.strip() for item in 参数列表.split('\n') if item.strip()])

In [ ]:
# 这下面的是用于初始化一些值或者环境变量的，轻易别改
frpcStartArg = ''
reLoad = True

!mkdir -p $install_path/configFiles
if Path(frp配置文件或配置.strip()).exists():
    frpcConfigFile = frp配置文件或配置.strip()
if not Path(frpcConfigFile).exists(): 
    if frp配置文件或配置.strip().startswith('-f'):
        frpcStartArg = frp配置文件或配置.strip()
    else:
        useFrpc = False
else:
    os.system(f'cp -f {frpcConfigFile} {install_path}/configFiles/frpc_webui.ini')
    frpcConfigFile = f'{install_path}/configFiles/frpc_webui.ini'
    os.system(f'sed -i "s/local_port = .*/local_port = {w_Port}/g" {frpcConfigFile}')
    frpcStartArg = f' -c {frpcConfigFile}'

ngrokToken=''
if Path(ngrok配置或文件地址.strip()).exists():
    ngrokTokenFile = ngrok配置或文件地址.strip()
if Path(ngrokTokenFile).exists():
    with open(ngrokTokenFile,encoding = "utf-8") as nkfile:
        ngrokToken = nkfile.readline()
elif not ngrok配置或文件地址.strip().startswith('/'):
    ngrokToken=ngrok配置或文件地址.strip()
    

# kaggle public API

**不能使用%cd这种会改变当前工作目录的命令，会导致和其他线程冲突**

---

In [ ]:
# 安装kaggle的api token文件
def initKaggleConfig():
    if Path('~/.kaggle/kaggle.json').exists():
        return True
    if Path(kaggleApiTokenFile).exists():
        !mkdir -p ~/.kaggle/
        os.system('cp '+kaggleApiTokenFile+' ~/.kaggle/kaggle.json')
        !chmod 600 ~/.kaggle/kaggle.json
        return True
    print('缺少kaggle的apiToken文件，访问：https://www.kaggle.com/你的kaggle用户名/account 获取')
    return False

def getUserName():
    if not initKaggleConfig(): return
    import kaggle
    return kaggle.KaggleApi().read_config_file()['username']

def createOrUpdateDataSet(path:str,datasetName:str):
    if not initKaggleConfig(): return
    print('创建或更新数据集 '+datasetName)
    import kaggle
    os.system('mkdir -p $install_path/kaggle_cache')
    os.system('rm -rf $install_path/kaggle_cache/*')
    datasetDirPath = install_path+'/kaggle_cache/'+datasetName
    os.system('mkdir -p '+datasetDirPath)
    os.system('cp -f '+path+' '+datasetDirPath+'/')
    username = getUserName()
    print("kaggle username:"+username)
    datasetPath = username+'/'+datasetName
    datasetList = kaggle.api.dataset_list(mine=True,search=datasetPath)
    print(datasetList)
    if len(datasetList) == 0 or datasetPath not in [str(d) for d in datasetList]: # 创建 create
        os.system('kaggle datasets init -p' + datasetDirPath)
        metadataFile = datasetDirPath+'/dataset-metadata.json'
        os.system('sed -i s/INSERT_TITLE_HERE/'+ datasetName + '/g ' + metadataFile)
        os.system('sed -i s/INSERT_SLUG_HERE/'+ datasetName + '/g ' + metadataFile)
        os.system('cat '+metadataFile)
        os.system('kaggle datasets create -p '+datasetDirPath)
        print('create database done')
    else:
        kaggle.api.dataset_metadata(datasetPath,datasetDirPath)
        kaggle.api.dataset_create_version(datasetDirPath, 'auto update',dir_mode='zip')
        print('upload database done')

def downloadDatasetFiles(datasetName:str,outputPath:str):
    if not initKaggleConfig(): return
    print('下载数据集文件 '+datasetName)
    import kaggle
    username = getUserName()
    datasetPath = username+'/'+datasetName
    datasetList = kaggle.api.dataset_list(mine=True,search=datasetPath)
    if datasetPath not in [str(d) for d in datasetList]:
        return False
    os.system('mkdir -p '+outputPath)
    kaggle.api.dataset_download_files(datasetPath,path=outputPath,unzip=True)
    return True



# 工具函数
**不能使用%cd这种会改变当前工作目录的命令，会导致和其他线程冲突**

---

In [ ]:
# 绕过 os.systen 的限制执行命令
def run(shell:str,shellName=''):
    if shellName == '': shellName = str(time.time())
    !mkdir -p $install_path/run_cache
    with open(install_path+'/run_cache/run_cache.'+shellName+'.sh','w') as sh:
        sh.write(shell)
    !bash {install_path}/run_cache/run_cache.{shellName}.sh

# 连接多个路径字符串 让路径在shell命令中能正常的执行
def pathJoin(*paths:str):
    pathStr = ''
    for p in paths:
        pathStr += '"'+p+'"'
    pathStr = '"*"'.join(pathStr.split('*'))
    pathStr = '"$"'.join(pathStr.split('$'))
    pathStr = '"("'.join(pathStr.split('('))
    pathStr = '")"'.join(pathStr.split(')'))
    pathStr = '"{"'.join(pathStr.split('{'))
    pathStr = '"}"'.join(pathStr.split('}'))
    pathStr = re.sub(r'""','',pathStr)
    pathStr = re.sub(r'\*{2,}','"',pathStr)
    pathStr = re.sub(r'/{2,}','/',pathStr)
    pathStr = re.sub(r'/\./','/',pathStr)
    return pathStr

# 判断路径是不是一个文件或者可能指向一些文件
def pathIsFile(path):
    if Path(path).is_file():
        return True
    if re.search(r'\.(ckpt|safetensors|png|jpg|txt|pt|pth|json|yaml|\*)$',path):
        return True
    return False

def echoToFile(content:str,path:str):
    with open(path,'w') as sh:
        sh.write(content)

# ngrok
def startNgrok(ngrokToken:str,ngrokLocalPort:int):
    from pyngrok import conf, ngrok
    try:
        conf.get_default().auth_token = ngrokToken
        conf.get_default().monitor_thread = False
        ssh_tunnels = ngrok.get_tunnels(conf.get_default())
        if len(ssh_tunnels) == 0:
            ssh_tunnel = ngrok.connect(ngrokLocalPort)
            print('address：'+ssh_tunnel.public_url)
        else:
            print('address：'+ssh_tunnels[0].public_url)
    except:
        print('启动ngrok出错')
        
def startFrpc(name,configFile):
    run(f'''
cd $install_path/frpc/
$install_path/frpc/frpc {configFile}
        ''',name)
        
def installProxyExe():
    if useFrpc:
        print('安装frpc')
        !mkdir -p $install_path/frpc
        if Path(frpcExePath).exists():
            os.system(f'cp -f -n {frpcExePath} $install_path/frpc/frpc')
        else:
            !wget "https://huggingface.co/datasets/ACCA225/Frp/resolve/main/frpc" -O $install_path/frpc/frpc
        
        for ssl in frpcSSLFFlies:
            if Path(ssl).exists():
                os.system('cp -f -n '+pathJoin(ssl,'/*')+' $install_path/frpc/')
        !chmod +x $install_path/frpc/frpc
        !$install_path/frpc/frpc -v
    if useNgrok:
        %pip install pyngrok
    
def startProxy():
    if useNgrok:
        startNgrok(ngrokToken,w_Port)
    if useFrpc:
        startFrpc('frpc_proxy',frpcStartArg)

    
def zipPath(path:str,zipName:str,format='tar'):
    if path.startswith('$install_path'):
        path = path.replace('$install_path',install_path)
    if path.startswith('$output_path'):
        path = path.replace('$install_path',output_path)
    if not path.startswith('/'):
        path = pathJoin(install_path,'/stable-diffusion-webui','/',path)
    if Path(path).exists():
        if 'tar' == format:
            os.system('tar -cf $output_path/'+ zipName +'.tar -C '+ path +' . ')
        elif 'gz' == format:
            os.system('tar -czf $output_path/'+ zipName +'.tar.gz -C '+ path +' . ')
        return
    print('指定的目录不存在：'+path)


In [ ]:
# 解压保存的图片
# import zipfile

# def extract_archive(archive_path, password, dest_dir):
#     with zipfile.ZipFile(archive_path) as zf:
#         zf.extractall(path=dest_dir, pwd=password.encode())
        
# def create_archive(source_path, password, archive_path):
#     with zipfile.ZipFile(archive_path, mode='w', compression=zipfile.ZIP_DEFLATED) as zf:
#         for root, dirs, files in os.walk(source_path):
#             for file in files:
#                 file_path = os.path.join(root, file)
#                 zf.write(file_path, arcname=os.path.relpath(file_path, source_path), compress_type=zipfile.ZIP_DEFLATED)
#     zf.setpassword(password.encode())

# unzip_save():
#     if Path('/kaggle/working/output/log.zip').exists():
#         extract_archive('/kaggle/working/output/log.zip',加密密码.strip(),f'{install_path}/stable-diffusion-webui/log')

# save_to_zip():
#     if Path('/kaggle/working/output/log.zip').exists():
        


In [ ]:
import os
import re
import requests

def download_file(url, filename, path):
    # 获取文件的真实文件名
    if not filename:
        with requests.get(url, stream=True) as r:
            if 'Content-Disposition' in r.headers:
                filename = r.headers['Content-Disposition'].split('filename=')[1].strip('"')
            r.close()
    filename = re.sub(r'[\\/:*?"<>|;]', '', filename)
    # 拼接文件的完整路径
    filepath = os.path.join(path, filename)
    # 判断文件是否已存在
    if os.path.exists(filepath):
        print(f'{filename} already exists in {path}')
        return
    # 下载文件
    with requests.get(url, stream=True) as r:
        r.raise_for_status()
        with open(filepath, 'wb') as f:
            for chunk in r.iter_content(chunk_size=8192):
                if chunk:
                    f.write(chunk)
    print(f'{filename} has been downloaded to {path}')
    
# 加入文件到下载列表
def putDownloadFile(url:str,distDir:str,file_name:str=None):
    if re.match(r'^[^:]+:(https?|ftps?)://', url, flags=0):
        file_name = re.findall(r'^[^:]+:',url)[0][:-1]
        url = url[len(file_name)+1:]
    if not re.match(r'^(https?|ftps?)://',url):
        return
    file_name = re.sub(r'\s+','_',file_name or '')
    dir = str(hash(url)).replace('-','')
    down_dir = f'{install_path}/down_cache/{dir}'
    !mkdir -p {down_dir}
    return [url,file_name,distDir,down_dir]

def get_file_size_in_gb(file_path):
    size_in_bytes = Path(file_path).stat().st_size
    size_in_gb = size_in_bytes / (1024 ** 3)
    return '%.2f' % size_in_gb
    
# 下载文件
def startDownloadFiles(download_list):
    print('下载列表:\n','\n'.join([f'{item[0]} -> {item[2]}/{item[1]}' for item in download_list]))
    dist_list = []
    for dow_f in download_list:
        !mkdir -p {dow_f[3]}
        print('下载 名称：',dow_f[1],'url：',dow_f[0])
        download_file(dow_f[0],dow_f[1],dow_f[2])

# webui 安装和配置函数
---

In [ ]:
envInstalled=False
extensionsDone=False

#安装webui
def install():
    print('安装webui')
    %cd $install_path
    if reLoad:
        !rm -rf stable-diffusion-webui
    if Path("stable-diffusion-webui").exists():
        %cd $install_path/stable-diffusion-webui/
        !git checkout .
        !git pull
    else:
        if mobileOptimize:
            !git clone https://github.com/viyiviyi/stable-diffusion-webui.git stable-diffusion-webui -b local  # 修改了前端界面，手机使用更方便
        else:
            !git clone https://github.com/AUTOMATIC1111/stable-diffusion-webui stable-diffusion-webui
    print('安装webui 完成')

# 链接输出目录
def link_dir():
    print('链接输出目录')
    # 链接输出目录 因为sd被部署在了stable-diffusion-webui目录，运行结束后为了方便下载就只有outputs目录放在output_path/目录下
    !mkdir -p $output_path/outputs
    !rm -rf $install_path/stable-diffusion-webui/outputs
    !ln -s -r $output_path/outputs $install_path/stable-diffusion-webui/ # 输出目录
    !mkdir -p $output_path/log
    !rm -rf $install_path/stable-diffusion-webui/log
    !ln -s -r $output_path/log $install_path/stable-diffusion-webui/
    # 链接 hypernetworks 目录
    if linkHypernetworksDir:
        !rm -rf $install_path/stable-diffusion-webui/models/hypernetworks
        !mkdir -p $output_path/hypernetworks
        !ln -s -r $output_path/hypernetworks $install_path/stable-diffusion-webui/models/
    # 链接 embeddings 目录
    if linkEmbeddingsDir:
        !rm -rf $install_path/stable-diffusion-webui/embeddings
        !mkdir -p $output_path/embeddings
        !ln -s -r $output_path/embeddings $install_path/stable-diffusion-webui/
    # 链接训练输出目录 文件夹链接会导致功能不能用
    if linkTextual_inversionDir:
        !rm -rf $install_path/stable-diffusion-webui/textual_inversion
        !mkdir -p $output_path/textual_inversion/
        !ln -s -r $output_path/textual_inversion $install_path/stable-diffusion-webui/
    print('链接输出目录 完成')
    
# 链接模型文件
def load_models(skip_url=False):
    print(('复制' if enableLoadByCopy else '链接') + '模型文件')
    if enableLoadByCopy:
        print('如果出现 No such file or directory 错误，可以忽略')
    download_list = []
    models_dir_path = f'{install_path}/stable-diffusion-webui/models/Stable-diffusion'
    hypernetworks_dir_path = f'{install_path}/stable-diffusion-webui/models/hypernetworks'
    embeddings_dir_path = f'{install_path}/stable-diffusion-webui/embeddings'
    lora_dir_path = f'{install_path}/stable-diffusion-webui/models/Lora'
    lycoris_dir_path = f'{install_path}/stable-diffusion-webui/models/LyCORIS'
    vae_dir_path = f'{install_path}/stable-diffusion-webui/models/VAE'
    control_net_dir_path = f'{install_path}/stable-diffusion-webui/extensions/sd-webui-controlnet/models'
    
    def link_file(source_paths,dist:str):
        !mkdir -p {dist}
        for path in source_paths:
            if 'https://' in path or 'http://' in path:
                if skip_url:
                    continue
                download_list.append(putDownloadFile(path,dist))
            elif pathIsFile(path):
                os.system(('cp -n' if enableLoadByCopy else 'ln -s')+' -f '+ pathJoin(path) +f' {dist}')
            else:
                os.system(('cp -n' if enableLoadByCopy else 'ln -s')+' -f '+ pathJoin(path,'/*.*') +f' {dist}')
        !rm -f {dist}/\*.* 
                  
    link_file(modelDirs,models_dir_path)
    link_file(hypernetworksModelDirs,hypernetworks_dir_path)
    link_file(embeddingsModelDirs,embeddings_dir_path)
    link_file(loraModelDirs,lora_dir_path)
    link_file(lyCORISModelDirs,lycoris_dir_path)
    link_file(modelVaeDirs,vae_dir_path)
    link_file(controlNetModels,control_net_dir_path)
    startDownloadFiles([item for item in download_list if item])
    print(('复制' if enableLoadByCopy else '链接') + '模型文件 完成')

#安装依赖
def install_dependencies():
    print('安装webui需要的python环境')
    global envInstalled
    sh = f'cd {install_path}/stable-diffusion-webui\n'
    if str(sys.version).startswith('3.8') or str(sys.version).startswith('3.9') or str(sys.version).startswith('3.10'):
        sh += '''
python3 -m venv venv
'''
    else:
        sh += '''
add-apt-repository ppa:deadsnakes/ppa -y
apt update
apt install python3.10 -y
python3.10 -m venv venv
'''
    if quickStart and Path(venvPath).exists():
        sh += 'echo "unzip venv"\n'
        sh += f'tar -xf {venvPath} -C ./venv\n'
    sh += '\n'
    run(sh,'dependencies')
    if not Path(f'{install_path}/stable-diffusion-webui/venv/bin/pip').exists():
        !curl https://bootstrap.pypa.io/get-pip.py -o get-pip.py
        !{install_path}/stable-diffusion-webui/venv/bin/python3 get-pip.py
        
    !{install_path}/stable-diffusion-webui/venv/bin/python3 -V
    !{install_path}/stable-diffusion-webui/venv/bin/python3 -m pip -V
    
    if not quickStart or not Path(venvPath).exists():
        !{install_path}/stable-diffusion-webui/venv/bin/python3 -m pip install -U torch==2.0.0+cu117 torchvision==0.15.1+cu117 torchaudio==2.0.1 --index-url https://download.pytorch.org/whl/cu117
        !{install_path}/stable-diffusion-webui/venv/bin/python3 -m pip install -U open-clip-torch xformers==0.0.19
    
    envInstalled = True
    print('安装webui需要的python环境 完成')

# 安装插件
def install_extensions():
    global extensionsDone
    print('安装插件')
    sh = 'mkdir -p $install_path/stable-diffusion-webui/extensions \n'
    sh = 'mkdir -p $install_path/cache/extensions \n'
    sh += 'cd $install_path/cache/extensions \n'
    for ex in extensions:
        sh += 'git clone ' + ex + ' \n'
    sh += 'rsync -a $install_path/cache/extensions/* $install_path/stable-diffusion-webui/extensions \n'
    sh += 'cd ../ && rm -rf $install_path/cache/extensions \n'
    run(sh,'extensions')
    extensionsDone = True
    print('安装插件 完成')
    
# 个性化配置 
def use_config():
    print('使用自定义配置 包括tag翻译 \n')
    %cd $install_path/stable-diffusion-webui
    !mkdir -p tmp
    %cd tmp
    !git clone {webui_settings} sd-configs
    !cp -rf sd-configs/dist/* $install_path/stable-diffusion-webui
    if not Path(ui_config_file).exists(): # ui配置文件
        !mkdir -p {ui_config_file[0:ui_config_file.rfind('/')]}
        os.system('cp -f -n $install_path/stable-diffusion-webui/ui-config.json '+ui_config_file)
    if not Path(setting_file).exists(): # 设置配置文件
        !mkdir -p {setting_file[0:setting_file.rfind('/')]}
        os.system('cp -f -n $install_path/stable-diffusion-webui/config.json '+setting_file)

def checkDefaultModel():
    print('检查默认模型文件是否存在 \n')
    global usedCkpt
    if usedCkpt is not None and usedCkpt != '': # 设置启动时默认加载的模型
        if '.' in usedCkpt:
            if '/' in usedCkpt:
                usedCkpt = usedCkpt
            else:
                usedCkpt = install_path + '/stable-diffusion-webui/models/Stable-diffusion/' + usedCkpt
        else:
            for x in ['.ckpt','.safetensors']:
                if Path(install_path+'/stable-diffusion-webui/models/Stable-diffusion/' + usedCkpt+x).exists():
                    usedCkpt = install_path+'/stable-diffusion-webui/models/Stable-diffusion/' + usedCkpt+x
                    break
    if Path(usedCkpt).exists():
        return True
    else:
        if Path(usedCkpt).is_symlink():
            print('模型文件真实地址：'+os.readlink(usedCkpt))
        return False

# 启动
def start():
    print('启动webui')
    %cd $install_path/stable-diffusion-webui
    args = ' --port=' + str(w_Port)
    if not disableShared:
        args += ' --share'
    if onlyApi:
        args += ' --nowebui'
    if ui_config_file is not None and ui_config_file != '' and Path(ui_config_file).exists(): # ui配置文件
        args += ' --ui-config-file=' + pathJoin(ui_config_file)
    if setting_file is not None and setting_file != '' and Path(setting_file).exists(): # 设置配置文件
        args += ' --ui-settings-file=' + pathJoin(setting_file)
    if not checkDefaultModel():
        print('默认模型文件不存在，请检查配置：'+usedCkpt)
    else:
        args += ' --ckpt='+ pathJoin(usedCkpt)
    if vaeHalf is False: 
        args += ' --no-half-vae'
    if modelHalf is False:
        args += ' --no-half'
    if consoleProgressbars is False:
        args += ' --disable-console-progressbars'
    if consolePrompts is True:
        args += ' --enable-console-prompts'
    args += ' ' + otherArgs
    os.environ['COMMANDLINE_ARGS']=args
    !echo COMMANDLINE_ARGS=$COMMANDLINE_ARGS
    %env REQS_FILE=requirements.txt
    # 只要不爆内存，其他方式关闭后会再次重启 访问地址会发生变化
    if useFrpc:
        while True:
            !venv/bin/python3 launch.py
            print('5秒后重启webui')
            time.sleep(5)
    else:
        !venv/bin/python3 launch.py
    

# 入口函数
---

In [ ]:
# 启动非webui相关的的内容，加快启动速度
def main():
    global envInstalled
    global extensionsDone
    startTicks = time.time()
    isInstall = True if os.getenv('IsInstall','False') == 'True' else False
    if isInstall is False or reLoad: 
        install()
        if enableThread:
            threading.Thread(target = install_extensions,daemon=True).start()
            threading.Thread(target = load_models,daemon=True).start()
            threading.Thread(target = install_dependencies,daemon=True).start()
        else:
            install_extensions()
            load_models()
            install_dependencies()
        t = 0
        while not envInstalled or not extensionsDone:
            if t%10==0:
                print('等待python环境和插件安装...')
            t = t+1
            time.sleep(1)
        link_dir()
        use_config()
        installProxyExe()
        threading.Thread(target = startProxy,daemon=True).start()
        os.environ['IsInstall'] = 'True'
    else:
        envInstalled = True
        extensionsDone = True
    load_models(True)
    ticks = time.time()
    print("加载耗时:",(ticks - startTicks),"秒")
    start()


# 执行区域
---

In [ ]:
# 如果需要重新安装，请注释这一行
reLoad = False
# 启动
main()